## Setup 

### Import packages

In [3]:
%matplotlib inline
%reload_ext autoreload
%autoreload

In [7]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import matplotlib
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
import plotly.io as pio
from plotly import tools

from copy import copy
import scipy
from sklearn import svm

# Disable numpy warnings
import warnings
warnings.simplefilter(action="ignore", category=FutureWarning)

### Load data
Load data from the `./data/interim/` folder and parse into `pandas` dataframes.

In [8]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_profile_features = df_from_csv('profile_features.csv', index_col=[0])

impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }

twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}

print('Done!')

Importing profiles.csv
Importing profile_features.csv
Importing impacts_forecasted_foreshore_slope_sto06.csv
Importing impacts_forecasted_mean_slope_sto06.csv
Importing impacts_observed.csv
Importing twl_foreshore_slope_sto06.csv
Importing twl_mean_slope_sto06.csv
Done!


## Difference between $R_{high}$ and $D_{low}$
Since the Storm Impact Regime is so dependant on the predicted $R_{high}$ and obsereved $D_{low}$ levels, let's investigate the difference between these two variables in more detail.



### Gather data

First, let's split the `site_ids` by whether we observed swash or collision and by whether we predicted swash or collision. We want to identify if there are any difference between these four groups.

In [10]:
def get_site_ids(df_forecasted, df_observed, forecasted_regime,
                 observed_regime):
    """
    Returns list of site_ids which match the given forecasted and observed regime
    """
    set1 = set(
        df_forecasted.query("storm_regime == '{}'".format(forecasted_regime)).
        index.get_level_values('site_id'))
    set2 = set(
        df_observed.query("storm_regime == '{}'".format(observed_regime)).
        index.get_level_values('site_id'))
    return sorted(list(set1.intersection(set2)))


def get_R_high_D_low_diff(site_ids, df_profile_features, df_twls):
    """
    Returns a dataframe of the difference between the R_high and D_low differences. 
    Positive values indicate R_high is larger than D_low.
    """
    # Get dune toes at these sites and predicted max R_high
    df_toes = df_profile_features.loc[site_ids].query(
        'profile_type=="prestorm"').dune_toe_z
    df_R_highs = df_twls.loc[site_ids].groupby('site_id')['R_high'].max()

    # Join into one dataframe
    df_twl_toes = pd.concat([df_toes, df_R_highs], axis=1, sort=True)
    df_twl_toes['diff'] = df_twl_toes['R_high'] - df_twl_toes['dune_toe_z']
    return df_twl_toes['diff']

In [15]:
# Identify sites where swash regime was correctly or overpredicted

swash_overpredicted_site_ids = get_site_ids(
    df_forecasted=impacts['forecasted']['mean_slope_sto06'],
    df_observed=impacts['observed'],
    forecasted_regime='collision',
    observed_regime='swash')
swash_overpredicted_diffs = get_R_high_D_low_diff(
    site_ids=swash_overpredicted_site_ids,
    df_profile_features=df_profile_features,
    df_twls=twls['forecasted']['mean_slope_sto06'])

swash_correct_site_ids = get_site_ids(
    df_forecasted=impacts['forecasted']['mean_slope_sto06'],
    df_observed=impacts['observed'],
    forecasted_regime='swash',
    observed_regime='swash')
swash_correct_diffs = get_R_high_D_low_diff(
    site_ids=swash_correct_site_ids,
    df_profile_features=df_profile_features,
    df_twls=twls['forecasted']['mean_slope_sto06'])

In [14]:
# Identify sites where collision regime was correctly or underpredicted

collision_underpredicted_site_ids = get_site_ids(
    df_forecasted=impacts['forecasted']['mean_slope_sto06'],
    df_observed=impacts['observed'],
    forecasted_regime='swash',
    observed_regime='collision')
collision_underpredicted_diffs = get_R_high_D_low_diff(
    site_ids=collision_underpredicted_site_ids,
    df_profile_features=df_profile_features,
    df_twls=twls['forecasted']['mean_slope_sto06'])

collision_correct_site_ids = get_site_ids(
    df_forecasted=impacts['forecasted']['mean_slope_sto06'],
    df_observed=impacts['observed'],
    forecasted_regime='collision',
    observed_regime='collision')
collision_correct_diffs = get_R_high_D_low_diff(
    site_ids=collision_correct_site_ids,
    df_profile_features=df_profile_features,
    df_twls=twls['forecasted']['mean_slope_sto06'])

### Plot difference in $R_{high}$ and $D_{low}$ for swash and collision regimes
What does the distribution of elevations look like for when we observe swash and collision regimes? Are there any difference between correctly and incorrectly predicted swash regime impacts?

In [12]:
trace1 = go.Histogram(
    y=swash_correct_diffs.tolist(),
    opacity=0.75,
    name='Correctly predicted',
    marker=dict(color='#67a9cf', ),
    ybins=dict(size=0.1),
)
trace2 = go.Histogram(
    y=swash_overpredicted_diffs.tolist(),
    opacity=0.75,
    name='Overpredicted',
    marker=dict(color='#ef8a62', ),
    ybins=dict(size=0.1),
)

layout = go.Layout(
    title='R_high - D_low<br>Swash Regime',
    barmode='overlay',
    yaxis=dict(title='z (m AHD)'),
    xaxis=dict(title='Count'),
    bargap=0.2,
    bargroupgap=0.1,
    legend=dict(x=.6, y=1))

g_plot_swash = go.FigureWidget(data=[trace2, trace1], layout=layout)

# To output to file
img_bytes = pio.write_image(
    g_plot_swash,
    '02_R_high_D_low_swash.png',
    format='png',
    width=600,
    height=400,
    scale=5)

g_plot_swash

FigureWidget({
    'data': [{'marker': {'color': '#ef8a62'},
              'name': 'Overpredicted',
          …

The plot above shows that when $R_{high}$ - $D_{low}$ is $<0$, swash is correctly predicted. This is by definition, so is not surprising. The biggest occurance of $R_{high}$ - $D_{low}$ is slightly below $0$, so it appears that we have correctly predicted a majority of the observed swash regime events. 

Let's do the same thing, now considering `site_ids` where we have observed collision.

In [16]:
trace1 = go.Histogram(
    y=collision_correct_diffs.tolist(),
    opacity=0.75,
    name='Correctly predicted',
    marker=dict(color='#67a9cf', ),
    ybins=dict(size=0.1),
)
trace2 = go.Histogram(
    y=collision_underpredicted_diffs.tolist(),
    opacity=0.75,
    name='Underpredicted',
    marker=dict(color='#ef8a62', ),
    ybins=dict(size=0.1),
)

layout = go.Layout(
    title='R_high - D_low<br>Collision Regime',
    barmode='overlay',
    yaxis=dict(title='z (m AHD)'),
    xaxis=dict(title='Count'),
    bargap=0.2,
    bargroupgap=0.1,
    legend=dict(x=.6, y=1))

g_plot_collision = go.FigureWidget(data=[trace2, trace1], layout=layout)

# To output to file
img_bytes = pio.write_image(
    g_plot_collision,
    '02_R_high_D_low_collision.png',
    format='png',
    width=600,
    height=400,
    scale=5)

g_plot_collision

FigureWidget({
    'data': [{'marker': {'color': '#ef8a62'},
              'name': 'Underpredicted',
         …

We can see a trend similar to the swash regime, except flipped. A majority of the correctly forecasted collision regimes occur when $R_{high}$ - $D_{low}$ is $>0$, by definition. 

### TODO Does dune toe lower?
Is there any patterns that dictate whether the dune toe raises or lowers when subject to collision. Is it just based on the peak $R_{high}$ level, similar to equilibrium theory?


## Relationship between parameters
Let's further investigate the relationship between hydrodynamic and morphodynamic parameters and see if they can tell us any more about how the storm regime may be correctly or incorrectly predicted.

### Add functions for adding parameters to the dataframe
We need some additional functions which will add parameters to our dataframe so we can plot them.

In [25]:
def add_berm_width(df, df_profiles, df__profile_features):
    """
    Adds a new column to the dataframe, with the prestorm berm width
    """
    # Get x coorindates of dune toe and limit of survey (z=0)
    df_profile_end_x = df_profiles.query('profile_type=="prestorm"').dropna(
        subset=['z']).groupby('site_id').tail(1).reset_index(
            ['profile_type', 'x']).x.rename('x_end').to_frame()
    df_profile_dune_toe_x = df_profile_features.query(
        'profile_type=="prestorm"').dune_toe_x.to_frame()

    # Merge and take the difference to calculate berm width
    df_merged = df_profile_end_x.merge(
        df_profile_dune_toe_x, left_index=True, right_index=True)
    berm_width = (df_merged['x_end'] -
                  df_merged['dune_toe_x']).rename('berm_width').to_frame()

    # Return the dataframe with the berm_width col merged
    return df.merge(berm_width, left_index=True, right_index=True)


def add_observed_regime(df, df_observed, new_col='observed_storm_regime'):
    """
    Adds a new column to the dataframe, with the observed storm regime
    """
    return df.merge(
        impacts['observed'].storm_regime.rename(new_col).to_frame(),
        left_index=True,
        right_index=True)


def add_mean_slope(df, df_twl):
    """
    Adds a new column to the dataframe with prestorm mean slope
    """
    df_mean_slope = df_twl.groupby('site_id').first().beta.rename(
        'mean_slope').to_frame()
    return df.merge(df_mean_slope, left_index=True, right_index=True)


def add_prestorm_berm_vol(df, df_impacts_observed):
    """
    Adds a new column to the dataframe with prestorm berm volume
    """
    return df.merge(
        df_impacts_observed.prestorm_swash_vol.rename('prestorm_berm_vol').
        to_frame(),
        left_index=True,
        right_index=True)


def add_prediction_class(df_impacts, prediction_classes):
    """
    Adds a column which groups site_ids into the predicted and observed storm regime combination
    """
    for prediction_class in prediction_classes:
        df_impacts.loc[df_impacts.index.isin(prediction_class['site_ids']),
                       'prediction_class'] = prediction_class['class']
    return df_impacts

### Create the dataframe
We need to combine and add data into a single dataframe for comparison purposes.

In [26]:
# Start with the forecasted impact dataframe
df = impacts['forecasted']['mean_slope_sto06']

# Add a column which groups site_ids into the predicted and observed storm regime combination
prediction_classes = [
    {
        'site_ids': collision_underpredicted_site_ids,
        'class': 'collision_underpredicted'
    },
    {
        'site_ids': collision_correct_site_ids,
        'class': 'collision_correct'
    },
    {
        'site_ids': swash_overpredicted_site_ids,
        'class': 'swash_overpredicted'
    },
    {
        'site_ids': swash_correct_site_ids,
        'class': 'swash_correct'
    },
]
df = add_prediction_class(df, prediction_classes)

# Drop site_ids where we do not have a prediction class (caused by NaNs)
df = df.dropna(subset=['prediction_class'])

# Add additional parameters
df = add_observed_regime(df, impacts['observed'])
df = add_berm_width(df, df_profiles, df_profile_features)
df = add_mean_slope(df, df_twl=twls['forecasted']['mean_slope_sto06'])
df = add_prestorm_berm_vol(df, df_impacts_observed=impacts['observed'])
df['R_high_dune_toe_diff'] = df['R_high'] - df['dune_toe_z']
df['R_high_dune_toe_ratio'] = df['R_high'] / df['dune_toe_z']

### Create scatter plot matrix of parameter interactions
Plot each hydrodynamic and morphodynamic parameter against each other and see if we can identify any patterns.

In [46]:
# Setup colors for different classes
text = df['prediction_class'].tolist()
class_code = {x['class']: n for n, x in enumerate(prediction_classes)}
color_vals = [class_code[cl] for cl in df['prediction_class']]

# Each prediction class will have its own color
pl_colorscale = [[0.0, '#d7191c'], [0.25, '#d7191c'], [0.25, '#fdae61'],
                 [0.5, '#fdae61'], [0.5, '#2c7bb6'], [0.75, '#2c7bb6'],
                 [0.75, '#abd9e9'], [1, '#abd9e9']]

# Setup plotly scatterplot matrix
trace1 = go.Splom(
    dimensions=[
        dict(label='dune_toe_z', values=df['dune_toe_z']),
        dict(label='R_high', values=df['R_high']),
        dict(label='berm_width', values=df['berm_width']),
        dict(
            label='twl_dune_toe_z_exceedance_hrs',
            values=df['twl_dune_toe_z_exceedance_hrs']),
        dict(label='R_high_dune_toe_diff', values=df['R_high_dune_toe_diff']),
        dict(
            label='R_high_dune_toe_ratio', values=df['R_high_dune_toe_ratio']),
        dict(label='mean_slope', values=df['mean_slope']),
        dict(label='prestorm_berm_vol', values=df['prestorm_berm_vol']),
    ],
    text=text,
    diagonal=dict(visible=False),
    showupperhalf=False,
    marker=dict(
        color=color_vals,
        size=2,
        colorscale=pl_colorscale,
        showscale=False,
        line=dict(width=0.1, color='rgb(230,230,230)')))

axis = dict(showline=True, zeroline=False, gridcolor='#fff', ticklen=4)

layout = go.Layout(
    title='Storm Impact Scatter Plot Matrix',
    dragmode='select',
    width=800,
    height=800,
    autosize=False,
    hovermode='closest',
    plot_bgcolor='rgba(240,240,240, 0.95)',
    xaxis1=dict(axis),
    xaxis2=dict(axis),
    xaxis3=dict(axis),
    xaxis4=dict(axis),
    xaxis5=dict(axis),
    xaxis6=dict(axis),
    xaxis7=dict(axis),
    xaxis8=dict(axis),
    yaxis1=dict(axis),
    yaxis2=dict(axis),
    yaxis3=dict(axis),
    yaxis4=dict(axis),
    yaxis5=dict(axis),
    yaxis6=dict(axis),
    yaxis7=dict(axis),
    yaxis8=dict(axis),
)

# Change font of axis labels
for ax in layout:
    if 'xaxis' in ax or 'yaxis' in ax:
        layout[ax]['titlefont'] = {'size': 12}

fig_scatter = go.FigureWidget(data=[trace1], layout=layout)

# To output to file
img_bytes = pio.write_image(
    fig_scatter,
    '02_scatter_plot.png',
    format='png',
    width=1500,
    height=1500,
    scale=5)

Jupyter get's a little bit slow when trying to display this plot interactively, so let's output it as an image to view.
![02_scatter_plot.png](02_scatter_plot.png)

### Create parameter confusion matrix
It's a bit hard to see the difference between the different categories, lets do a confusion matrix but with plots showing two variables on each axis. First, list all the different parameters we have available to plot against:

In [33]:
df.columns

Index(['datetime', 'R_high', 'R_low', 'dune_toe_z', 'dune_crest_z',
       'storm_regime', 'twl_dune_toe_z_exceedance_hrs', 'prediction_class',
       'observed_storm_regime', 'berm_width', 'mean_slope',
       'prestorm_berm_vol', 'R_high_dune_toe_diff', 'R_high_dune_toe_ratio'],
      dtype='object')

In [34]:
# Define which columns we want to plot
x_col = 'prestorm_berm_vol'
y_col = 'R_high_dune_toe_diff'
marker_size = 4

# Create 2x2 subplot figure confusion matrix
fig = tools.make_subplots(
    rows=2,
    cols=2,
    vertical_spacing=0.09,
    subplot_titles=(
        'Predicted Swash',
        'Predicted Collision',
        '',
        '',
    ))

# Get data for all traces
x_all = df.loc[:, x_col]
y_all = df.loc[:, y_col]

# Create underlying grey traces of all data, so we can compare each subplot with the all the data.
trace5 = go.Scatter(
    mode='markers',
    x=x_all,
    y=y_all,
    showlegend=False,
    marker=dict(
        color='rgb(200,200,200)',
        size=marker_size,
    ))
fig.append_trace(trace5, 1, 1)

trace6 = copy(trace5)
trace6.xaxis = 'x2'
trace6.yaxis = 'y'
fig.append_trace(trace6, 1, 2)

trace7 = copy(trace5)
trace7.xaxis = 'x'
trace7.yaxis = 'y2'
fig.append_trace(trace7, 2, 1)

trace8 = copy(trace5)
trace8.xaxis = 'x2'
trace8.yaxis = 'y2'
fig.append_trace(trace8, 2, 2)

# Add actual data for each subplot

# Predicted swash, observed collision
trace1 = go.Scatter(
    mode='markers',
    x=df.loc[df.index.isin(collision_underpredicted_site_ids), x_col],
    y=df.loc[df.index.isin(collision_underpredicted_site_ids), y_col],
    marker=dict(
        color='#fc8d59',
        size=marker_size,
        line=dict(color='rgb(231,231,231)', width=0.5)))
fig.append_trace(trace1, 2, 1)

# Predicted collision, observed collision
trace2 = go.Scatter(
    mode='markers',
    x=df.loc[df.index.isin(collision_correct_site_ids), x_col],
    y=df.loc[df.index.isin(collision_correct_site_ids), y_col],
    marker=dict(
        color='#fc8d59',
        size=marker_size,
        line=dict(color='rgb(231,231,231)', width=0.5)))
fig.append_trace(trace2, 2, 2)

# Predicted swash, observed swash
trace3 = go.Scatter(
    mode='markers',
    x=df.loc[df.index.isin(swash_correct_site_ids), x_col],
    y=df.loc[df.index.isin(swash_correct_site_ids), y_col],
    marker=dict(
        color='#3182bd',
        size=marker_size,
        line=dict(color='rgb(231,231,231)', width=0.5)))
fig.append_trace(trace3, 1, 1)

# Predicted collision, observed swash
trace4 = go.Scatter(
    mode='markers',
    x=df.loc[df.index.isin(swash_overpredicted_site_ids), x_col],
    y=df.loc[df.index.isin(swash_overpredicted_site_ids), y_col],
    marker=dict(
        color='#3182bd',
        size=marker_size,
        line=dict(color='rgb(231,231,231)', width=0.5)))
fig.append_trace(trace4, 1, 2)

# Update formatting, titles, sizes etc.
fig['layout']['yaxis1'].update(
    title='{}<br>{}'.format('Observed swash', y_col))
fig['layout']['yaxis3'].update(
    title='{}<br>{}'.format('Observed collision', y_col))
fig['layout']['xaxis3'].update(title=x_col)
fig['layout']['xaxis4'].update(title=x_col)
fig['layout'].update(
    height=700, width=900, title='Storm Regime Confusion Matrix')
fig['layout']['showlegend'] = False
fig_to_plot = go.FigureWidget(data=fig.data, layout=fig.layout)

# To output to file
img_bytes = pio.write_image(
    fig_to_plot,
    '02_storm_regime_confusion.png',
    format='png',
    width=600,
    height=600,
    scale=5)

fig_to_plot

This is the format of your plot grid:
[ (1,1) x1,y1 ]  [ (1,2) x2,y2 ]
[ (2,1) x3,y3 ]  [ (2,2) x4,y4 ]



FigureWidget({
    'data': [{'marker': {'color': 'rgb(200,200,200)', 'size': 4},
              'mode': 'marker…

Plotting `prestorm_berm_vol` vs `R_high_dune_toe_diff` shows there is a difference between observed swash and collision. It appears when the `prestorm_berm_vol` is smaller than 80 m, we will get collision, regardless of whether `R_high_dune_toe_diff` is greater than 0 m. Let's confirm that there it is a vertical line to differentiate between these two regimes.

### Create regime predictor which includes berm volume

The technique for finding the boundary between two clusters is taken from [StackExchange](https://stackoverflow.com/a/22356267).

In [36]:
# Get data
df = df.dropna(subset=['prestorm_berm_vol', 'R_high_dune_toe_diff'])

swash_x = df.query('observed_storm_regime=="swash"').prestorm_berm_vol
swash_y = df.query('observed_storm_regime=="swash"').R_high_dune_toe_diff
swash_samples = np.array([[x, y] for x, y in zip(swash_x, swash_y)])

collision_x = df.query('observed_storm_regime=="collision"').prestorm_berm_vol
collision_y = df.query(
    'observed_storm_regime=="collision"').R_high_dune_toe_diff
collision_samples = np.array(
    [[x, y] for x, y in zip(collision_x, collision_y)])

# Fit SVM
X = np.concatenate((swash_samples, collision_samples), axis=0)
Y = np.array([0] * swash_x.shape[0] + [1] * collision_x.shape[0])

C = 1.0  # SVM regularization parameter
clf = svm.SVC(kernel='linear', gamma=0.7, C=C)
clf.fit(X, Y)

w = clf.coef_[0]
a = -w[0] / w[1]
y_vals = swash_y.tolist() + collision_y.tolist()
yy = np.linspace(min(y_vals), max(y_vals))
xx = (yy + (clf.intercept_[0]) / w[1]) / a

# Prepare plot
trace_swash = go.Scatter(
    x=swash_x,
    y=swash_y,
    name='Swash',
    mode='markers',
    marker=dict(
        color='#3182bd',
        size=marker_size,
        line=dict(color='rgb(231,231,231)', width=0.5)))

trace_collision = go.Scatter(
    x=collision_x,
    y=collision_y,
    name='Collision',
    mode='markers',
    marker=dict(
        color='#fc8d59',
        size=marker_size,
        line=dict(color='rgb(231,231,231)', width=0.5)))

trace_split = go.Scatter(
    x=xx,
    y=yy,
    name='Split (y={:.1f}x-{:.1f})'.format(a, (clf.intercept_[0]) / w[1]),
)

layout = dict(
    title='Observed Swash/Collision Regime Split',
    xaxis=dict(title='Prestorm berm volume', ),
    yaxis=dict(title='R_high - D_low'),
    legend=dict(x=.6, y=1.))

fig_to_plot = go.FigureWidget(
    data=[trace_swash, trace_collision, trace_split], layout=layout)

# To output to file
img_bytes = pio.write_image(
    fig_to_plot,
    '02_storm_regime_split.png',
    format='png',
    width=600,
    height=600,
    scale=5)

fig_to_plot

FigureWidget({
    'data': [{'marker': {'color': '#3182bd', 'line': {'color': 'rgb(231,231,231)', 'width': 0.5…

Looking at the plot above, it appears when the `prestorm_berm_vol` is less than 80 m, then we should classify it as collision, even if wave runup does not reach the toe of the dune.

### Test new berm vol predictor

Now lets go back to our predicted forecasts and see if our confusion matrix improves if we adopt this new criteria for differentiating between swash and collision.

First define a custom function to get colormap for our confusion matrix.

In [ ]:
def matplotlib_to_plotly(cmap_name='RdYlGn', pl_entries=255):
    """
    Function to convert matplotlib colorscale to plotly
    """
    cmap = matplotlib.cm.get_cmap(cmap_name)
    h = 1.0 / (pl_entries - 1)
    pl_colorscale = []

    for k in range(pl_entries):
        C = list(map(np.uint8, np.array(cmap(k * h)[:3]) * 255))
        pl_colorscale.append([k * h, 'rgb' + str((C[0], C[1], C[2]))])

    return pl_colorscale

In [40]:
from sklearn.metrics import confusion_matrix

# Create colorscale
rdylgr = matplotlib_to_plotly()

# Add new column with our new prediction technique.
df.loc[df['prestorm_berm_vol'] * 2.7 - 221.1 <= df['R_high_dune_toe_diff'],
       'new_predicted_storm_regime'] = 'collision'
df.loc[df['prestorm_berm_vol'] * 2.7 - 221.1 > df['R_high_dune_toe_diff'],
       'new_predicted_storm_regime'] = 'swash'

# Get observed and forecasted regimes, and merge
observed_regimes = df.observed_storm_regime.rename(
    'observed_regime').to_frame()
forecasted_regimes = df.new_predicted_storm_regime.rename(
    'forecasted_regime').to_frame()
df_compare = pd.concat([observed_regimes, forecasted_regimes],
                       axis='columns',
                       names=['a', 'b'],
                       sort=True)
df_compare.dropna(axis='index', inplace=True)

# Create a confusion matrix based on the observed/forecasted regimes.
# Need to do some flipping and reversing to get it in the correct
# order for the plotly heatmap.
z = confusion_matrix(
    df_compare.observed_regime.tolist(),
    df_compare.forecasted_regime.tolist(),
    labels=['swash', 'collision', 'overwash', 'inundation'])
z = np.flip(z, axis=0)
z_list = list(reversed(z.tolist()))

# Make incorrect values negative, so they get assigned a different color.
# Better for visualization
z_neg_incorrect = np.flip(np.identity(4), axis=0)
z_neg_incorrect[z_neg_incorrect == 0] = -1
z_neg_incorrect = (z * z_neg_incorrect).tolist()

# Change the text on the heatmap so it also displays percentages.
z_with_pct = []
for row in z:
    new_row = []
    for val in row:
        new_row.append('{}<br>({}%)'.format(
            val, np.around(val / np.sum(z) * 100, 1)))
    z_with_pct.append(new_row)

# Create the heatmap figure
x = ['swash', 'collision', 'overwash', 'inundation']
y = list(reversed(x))
fig = ff.create_annotated_heatmap(
    z_neg_incorrect, x=x, y=y, annotation_text=z_with_pct, colorscale=rdylgr)
heatmap = go.FigureWidget(data=fig.data, layout=fig.layout)

# Update axis titles
heatmap.layout.xaxis.update(title='Predicted')
heatmap.layout.yaxis.update(title='Observed')

# Write to file
img_bytes = pio.write_image(
    heatmap,
    '02_confusion_matrix_berm_vol_predictor.png',
    format='png',
    width=600,
    height=600,
    scale=5)

heatmap

FigureWidget({
    'data': [{'colorscale': [[0.0, 'rgb(165, 0, 38)'], [0.003937007874015748,
                 …

## TODO Compare predicted and underpredicted profiles

Define a function for getting the average beach profile for a number of given site_ids:

In [224]:
def get_avg_profile(site_ids, debug=False):
    rows = []
    for n,site_id in enumerate(site_ids):
        profile = df_profiles.query("site_id == '{}' and profile_type == 'prestorm'".format(site_id))
        profile_z = np.array(profile.z.tolist())
        profile_x = np.array(profile.index.get_level_values('x').tolist())
        
        # Let's center the profile based on the z=0 location
        idx_last_z_val = max(np.argwhere(~np.isnan(profile_z)==True))[0]
        x_last_val = profile_x[idx_last_z_val]
        profile_x = [x - x_last_val for x in profile_x]
        
        # Put values into a dictionary
        for x,z in zip(profile_x, profile_z):
            rows.append({'x':x, 'z': z})

        # Return early for debugging
        if debug and n>3:
            break
        
    # Create dataframe from rows
    df = pd.DataFrame(rows)
    avg_profile = df.groupby('x').agg({'z': [np.nanmean, np.nanstd]}).reset_index()

    return {
        'x': avg_profile.x.tolist(),
        'z': avg_profile.z.nanmean.tolist(),
        'std': avg_profile.z.nanstd.tolist(),
        'n': n+1  # number of profiles
    }

Now, let's look at whether there is a difference between the average beach profile of correctly forecasted site_ids and incorrectly forecasted site_ids. First, looking at sites where we observed swash regime.

In [225]:
overpredicted = get_avg_profile(swash_overpredicted_site_ids)
correct = get_avg_profile(swash_correct_site_ids)

# Add mean profile
trace_overpredicted_mean = go.Scatter(
    x=overpredicted['x'],
    y=overpredicted['z'],
    opacity=1,
    mode='lines',
    name='Mean overpredicted profile (n={})'.format(overpredicted['n']),
    line=dict(
        color=('rgb(205, 0, 0)'),
        width=2)
)

trace_overpredited_std_top = go.Scatter(
    x=overpredicted['x'],
    y=np.add(overpredicted['z'], overpredicted['std']),
    opacity=1,
    hoverinfo='none',
    showlegend=False,
    mode='lines',
    line=dict(
        color=('rgb(205, 0, 0)'),
        width=0.5,
        dash='dash')
)

trace_overpredited_std_btm = go.Scatter(
    x=overpredicted['x'],
    y=np.subtract(overpredicted['z'], overpredicted['std']),
    opacity=1,
    hoverinfo='none',
    mode='lines',
    showlegend=False,
    line=dict(
        color=('rgb(205, 0, 0)'),
        width=0.5,
        dash='dash')
)

trace_correct_mean = go.Scatter(
    x=avg_correct_x,
    y=avg_correct_z,
    opacity=1,
    mode='lines',
    name='Mean correct profile (n={})'.format(correct['n']),
    line=dict(
        color=('rgb(0, 205, 0)'),
        width=2)
)

trace_correct_std_top = go.Scatter(
    x=avg_correct_x,
    y=np.add(avg_correct_z, avg_correct_std),
    opacity=1,
    hoverinfo='none',
    showlegend=False,
    mode='lines',
    line=dict(
        color=('rgb(0, 205, 0)'),
        width=0.5,
        dash='dash')
)

trace_correct_std_btm = go.Scatter(
    x=avg_correct_x,
    y=np.subtract(avg_correct_z, avg_correct_std),
    opacity=1,
    hoverinfo='none',
    mode='lines',
    showlegend=False,
    line=dict(
        color=('rgb(0, 205, 0)'),
        width=0.5,
        dash='dash')
)

layout = dict(showlegend=True,
              title='Observed Swash Impact Regime',
              legend=dict(x=.6, y=1),
              xaxis=dict(
                  range=[-150, 0]),
              yaxis=dict(
                  range=[0, 10]))

fig = go.FigureWidget(data=[trace_overpredicted_mean,
                            trace_overpredited_std_top,
                            trace_overpredited_std_btm,
                            trace_correct_mean,
                            trace_correct_std_top,
                            trace_correct_std_btm],
                      layout=layout)

# To output to file
img_bytes = pio.write_image(
    fig, 'mean_profiles_swash.png', format='png', width=600, height=600, scale=5)

fig

C:\Users\z5189959\Desktop\nsw-2016-storm-impact\.venv\lib\site-packages\pandas\core\groupby\groupby.py:1062: RuntimeWarning:

Mean of empty slice

C:\Users\z5189959\Desktop\nsw-2016-storm-impact\.venv\lib\site-packages\numpy\lib\nanfunctions.py:1545: RuntimeWarning:

Degrees of freedom <= 0 for slice.



NameError: name 'avg_correct_x' is not defined

We can see that the difference is pretty minimal. For cases where we predicted collision, but observed swash (overprediction), we see that overpredicted profiles are slightly more concave than correctly predicted sites.

In [ ]:
underpredicted = get_avg_profile(collision_underpredicted_site_ids)
correct = get_avg_profile(collision_correct_site_ids)

# Add mean profile
trace_underpredicted_mean = go.Scatter(
    x = underpredicted['x'],
    y= underpredicted['z'],
    opacity = 1,
    mode='lines',
    name='Mean underpredicted profile (n={})'.format(underpredicted['n']),
    line = dict(
        color = ('rgb(205, 0, 0)'),
        width = 2)
)

trace_underpredicted_std_top = go.Scatter(
    x = underpredicted['x'],
    y= np.add(underpredicted['z'],underpredicted['std']),
    opacity = 1,
    hoverinfo='none',
    showlegend=False,
    mode='lines',
    line = dict(
        color = ('rgb(205, 0, 0)'),
        width = 0.5,
        dash = 'dash')
) 

trace_underpredicted_std_btm = go.Scatter(
    x = underpredicted['x'],
    y= np.subtract(underpredicted['z'],underpredicted['std']),
    opacity = 1,
    hoverinfo='none',
    mode='lines',
    showlegend=False,
    line = dict(
        color = ('rgb(205, 0, 0)'),
        width = 0.5,
        dash = 'dash')
) 

trace_correct_mean = go.Scatter(
    x = avg_correct_x,
    y= avg_correct_z,
    opacity = 1,
    mode='lines',
    name='Mean correct profile (n={})'.format(correct['n']),
    line = dict(
        color = ('rgb(0, 205, 0)'),
        width = 2)
)

trace_correct_std_top = go.Scatter(
    x = avg_correct_x,
    y= np.add(avg_correct_z, avg_correct_std),
    opacity = 1,
    hoverinfo='none',
    showlegend=False,
    mode='lines',
    line = dict(
        color = ('rgb(0, 205, 0)'),
        width = 0.5,
        dash = 'dash')
) 

trace_correct_std_btm = go.Scatter(
    x = avg_correct_x,
    y= np.subtract(avg_correct_z, avg_correct_std),
    opacity = 1,
    hoverinfo='none',
    mode='lines',
    showlegend=False,
    line = dict(
        color = ('rgb(0, 205, 0)'),
        width = 0.5,
        dash = 'dash')
) 
    
layout = dict(showlegend=True,
             title='Observed Collision Impact Regime',
             legend=dict(x=.6, y=1),
             xaxis=dict(
             range=[-150,0]),
             yaxis=dict(
             range=[0,10]))
    
fig=go.FigureWidget(data=[trace_underpredicted_mean, 
                          trace_underpredicted_std_top,
                          trace_underpredicted_std_btm, 
                          trace_correct_mean, 
                          trace_correct_std_top, 
                          trace_correct_std_btm], 
                    layout=layout)

# To output to file
img_bytes = pio.write_image(fig, 'mean_profiles_collision.png',format='png', width=600, height=600, scale=5)

fig



This plot is a bit more interesting. It shows that we are correctly forecasting collision when the profile is more accreted/convex, but when the profile is more eroded/concave, the water level is underpredicted. Why is this? 